# Coursera - Applied Data Science Capstone

### Introduction

As part of the final project we try to find the optimal location for opening a new Indian Restaurant in New York City.
We would try to find locations with low occurrences of an Indian restaurant in NYC. Also it would be ideal to have these locations in neighborhoods with high demands for restaurants.  
In order to find these locations we look at the number of existing restaurants as a proxy for demand.d

### Data
We would need the following information:
1. Neighborhood information: The latitudes and longitudes of the various neighborhoods in NYC.
2. Total number of restaurants in the various neighborhoods.
3. Number of Indian restaurants in the various neighborhoods.

We can get the neighborhood information from the below json files:  
https://cocl.us/new_york_dataset  
https://raw.githubusercontent.com/veltman/snd3/master/data/nyc-neighborhoods.geo.json

For the other two, we can use the Fourstone API calls to get the relevant information.

#### Downloading all the dependencies for the project.

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files


import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe


# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - folium=0.5.0


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    python_abi-3.6             |          1_cp36m           4 KB  conda-forge
    vincent-0.4.4              |             py_1          28 KB  conda-forge
    altair-4.1.0               |             py_1         614 KB  conda-forge
    folium-0.5.0               |             py_0          45 KB  conda-forge
    ca-certificates-2020.6.20  |       hecda079_0         145 KB  conda-forge
    branca-0.4.1               |             py_0          26 KB  conda-forge
    certifi-2020.6.20          |   py36h9f0ad1d_0         151 KB  conda-forge
    openssl-1.1.1g             |       h516909a_0         2.1 MB  conda-forge
    ------------------------------------------------------------
                       

#### Loading the data

We download the json file from the same source as the practice exercises.

In [126]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

Data downloaded!


In [127]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [128]:
newyork_data

{'type': 'FeatureCollection',
 'totalFeatures': 306,
 'features': [{'type': 'Feature',
   'id': 'nyu_2451_34572.1',
   'geometry': {'type': 'Point',
    'coordinates': [-73.84720052054902, 40.89470517661]},
   'geometry_name': 'geom',
   'properties': {'name': 'Wakefield',
    'stacked': 1,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661]}},
  {'type': 'Feature',
   'id': 'nyu_2451_34572.2',
   'geometry': {'type': 'Point',
    'coordinates': [-73.82993910812398, 40.87429419303012]},
   'geometry_name': 'geom',
   'properties': {'name': 'Co-op City',
    'stacked': 2,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.87429419303012]}},
  {'type': 'Feature',
 

In [129]:
neighborhoods_data = newyork_data['features']

In [130]:
neighborhoods_data[0:1]

[{'type': 'Feature',
  'id': 'nyu_2451_34572.1',
  'geometry': {'type': 'Point',
   'coordinates': [-73.84720052054902, 40.89470517661]},
  'geometry_name': 'geom',
  'properties': {'name': 'Wakefield',
   'stacked': 1,
   'annoline1': 'Wakefield',
   'annoline2': None,
   'annoline3': None,
   'annoangle': 0.0,
   'borough': 'Bronx',
   'bbox': [-73.84720052054902,
    40.89470517661,
    -73.84720052054902,
    40.89470517661]}}]

Converting the neighborhood data into a DataFrame

In [131]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

In [132]:
neighborhoods

Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude]
Index: []

In [133]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [134]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

Confirming that the Dataframe has 5 boroughs and 306 neighborhoods.

In [12]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


In [13]:
# Defining the latitude and longitude values of NYC for the map

latitude = 40.7127281
longitude = -74.0060152
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


### Creating a map of NYC with all the neighborhoods 

In [14]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

#### Defining Foursquare Credentials

In [228]:
# The code was removed by Watson Studio for sharing.

Defining a function to get the venues around our neighborhoods through looped calls to foresquare

In [16]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

Getting the venues data from foursquare using the above function

In [21]:
LIMIT = 100 # limit of number of venues returned by Foursquare API

radius = 500 # define radius

newyork_venues = getNearbyVenues(names=neighborhoods['Neighborhood'],
                                   latitudes=neighborhoods['Latitude'],
                                   longitudes=neighborhoods['Longitude']
                                  )




Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

In [22]:
print(newyork_venues.shape)
newyork_venues.head()

(10047, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

              Venue  Venue Latitude  Venue Longitude  Venue Category  
0  Lollipops Gelato       40.894123       -73.845892    Dessert Shop  
1         Walgreens       40.896528       -73.844700        Pharmacy  
2  Carvel Ice Cream       40.890487       -73.848568  Ice Cream Shop  
3          Rite Aid       40.896649       -73.844846        Pharmacy  
4           Dunkin'       40.890459       -73.849089      Donut Shop

In [23]:
newyork_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                               
Allerton                                      26                      26   
Annadale                                      13                      13   
Arden Heights                                  4                       4   
Arlington                                      5                       5   
Arrochar                                      20                      20   
Arverne                                       20                      20   
Astoria                                      100                     100   
Astoria Heights                               14                      14   
Auburndale                                    18                      18   
Bath Beach                                    47                      47   
Battery Park City                             63                      63   
Bay Ridge                                     86                      86   
Bay Terrace                                   49                      49   
Baychester                                    24                      24   
Bayside                                       75                      75   
Bayswater                                      2                       2   
Bedford Park                                  33                      33   
Bedford Stuyvesant                            30                      30   
Beechhurst                                    15                      15   
Bellaire                                      12                      12   
Belle Harbor                                  17                      17   
Bellerose                                     20                      20   
Belmont                                      100                     100   
Bensonhurst                                   35                      35   
Bergen Beach                                   5                       5   
Blissville                                    18                      18   
Bloomfield                                     4                       4   
Boerum Hill                                   87                      87   
Borough Park                                  22                      22   
Breezy Point                                   5                       5   
Briarwood                                      8                       8   
Brighton Beach                                44                      44   
Broad Channel                                  5                       5   
Broadway Junction                             17                      17   
Bronxdale                                     14                      14   
Brooklyn Heights                             100                     100   
Brookville                                     1                       1   
Brownsville                                   17                      17   
Bulls Head                                    49                      49   
Bushwick                                      79                      79   
Butler Manor                                   6                       6   
Cambria Heights                               14                      14   
Canarsie                                       6                       6   
Carnegie Hill                                 87                      87   
Carroll Gardens                              100                     100   
Castle Hill                                    7                       7   
Castleton Corners                             16                      16   
Central Harlem                                51                      51   
Charleston                                    29                      29   
Chelsea                                      107                     107   
Chinatown                                    100                     100   

In [24]:
print('There are {} uniques categories.'.format(len(newyork_venues['Venue Category'].unique())))

There are 425 uniques categories.


In [42]:
# one hot encoding
newyork_onehot = pd.get_dummies(newyork_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
newyork_onehot['Neighborhood'] = newyork_venues['Neighborhood'] 

# making neighborhood as the index
newyork_onehot.set_index('Neighborhood', inplace = True)

newyork_onehot.head()

Accessories Store  Adult Boutique  Afghan Restaurant  \
Neighborhood                                                         
Wakefield                     0               0                  0   
Wakefield                     0               0                  0   
Wakefield                     0               0                  0   
Wakefield                     0               0                  0   
Wakefield                     0               0                  0   

              African Restaurant  Airport Terminal  American Restaurant  \
Neighborhood                                                              
Wakefield                      0                 0                    0   
Wakefield                      0                 0                    0   
Wakefield                      0                 0                    0   
Wakefield                      0                 0                    0   
Wakefield                      0                 0                    0   

              Antique Shop  Arcade  Arepa Restaurant  Argentinian Restaurant  \
Neighborhood                                                                   
Wakefield                0       0                 0                       0   
Wakefield                0       0                 0                       0   
Wakefield                0       0                 0                       0   
Wakefield                0       0                 0                       0   
Wakefield                0       0                 0                       0   

              Art Gallery  Art Museum  Arts & Crafts Store  \
Neighborhood                                                 
Wakefield               0           0                    0   
Wakefield               0           0                    0   
Wakefield               0           0                    0   
Wakefield               0           0                    0   
Wakefield               0           0                    0   

              Arts & Entertainment  Asian Restaurant  Athletics & Sports  \
Neighborhood                                                               
Wakefield                        0                 0                   0   
Wakefield                        0                 0                   0   
Wakefield                        0                 0                   0   
Wakefield                        0                 0                   0   
Wakefield                        0                 0                   0   

              Auditorium  Australian Restaurant  Austrian Restaurant  \
Neighborhood                                                           
Wakefield              0                      0                    0   
Wakefield              0                      0                    0   
Wakefield              0                      0                    0   
Wakefield              0                      0                    0   
Wakefield              0                      0                    0   

              Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  Bakery  \
Neighborhood                                                               
Wakefield                   0          0           0           0       0   
Wakefield                   0          0           0           0       0   
Wakefield                   0          0           0           0       0   
Wakefield                   0          0           0           0       0   
Wakefield                   0          0           0           0       0   

              Bank  Bar  Baseball Field  Baseball Stadium  Basketball Court  \
Neighborhood                                                                  
Wakefield        0    0               0                 0                 0   
Wakefield        0    0               0                 0                 0   
Wakefield        0    0               0                 0                 0   
Wakefield        0    0            

In [46]:
# making a dataframe for just the restaurants
newyork_rest = newyork_onehot.filter(like='Restaurant',axis=1)


In [47]:
newyork_rest.head()

Afghan Restaurant  African Restaurant  American Restaurant  \
Neighborhood                                                               
Wakefield                     0                   0                    0   
Wakefield                     0                   0                    0   
Wakefield                     0                   0                    0   
Wakefield                     0                   0                    0   
Wakefield                     0                   0                    0   

              Arepa Restaurant  Argentinian Restaurant  Asian Restaurant  \
Neighborhood                                                               
Wakefield                    0                       0                 0   
Wakefield                    0                       0                 0   
Wakefield                    0                       0                 0   
Wakefield                    0                       0                 0   
Wakefield                    0                       0                 0   

              Australian Restaurant  Austrian Restaurant  \
Neighborhood                                               
Wakefield                         0                    0   
Wakefield                         0                    0   
Wakefield                         0                    0   
Wakefield                         0                    0   
Wakefield                         0                    0   

              Brazilian Restaurant  Cajun / Creole Restaurant  \
Neighborhood                                                    
Wakefield                        0                          0   
Wakefield                        0                          0   
Wakefield                        0                          0   
Wakefield                        0                          0   
Wakefield                        0                          0   

              Cambodian Restaurant  Cantonese Restaurant  \
Neighborhood                                               
Wakefield                        0                     0   
Wakefield                        0                     0   
Wakefield                        0                     0   
Wakefield                        0                     0   
Wakefield                        0                     0   

              Caribbean Restaurant  Caucasian Restaurant  Chinese Restaurant  \
Neighborhood                                                                   
Wakefield                        0                     0                   0   
Wakefield                        0                     0                   0   
Wakefield                        0                     0                   0   
Wakefield                        0                     0                   0   
Wakefield                        0                     0                   0   

              Colombian Restaurant  Comfort Food Restaurant  Cuban Restaurant  \
Neighborhood                                                                    
Wakefield                        0                        0                 0   
Wakefield                        0                        0                 0   
Wakefield                        0                        0                 0   
Wakefield                        0                        0                 0   
Wakefield                        0                        0                 0   

              Czech Restaurant  Dim Sum Restaurant  Dumpling Restaurant  \
Neighborhood                                                              
Wakefield                    0                   0                    0   
Wakefield                    0                   0                    0   
Wakefield                    0                   0                    0   
Wakefield                    0                   0                    0   
Wakefield                    0                   0                    0

In [89]:
# deleting all entries not having any restaurants
newyork_rest = newyork_rest[(newyork_rest.T != 0).any()]

In [94]:
newyork_rest.head()

Afghan Restaurant  African Restaurant  American Restaurant  \
Neighborhood                                                               
Co-op City                    0                   0                    0   
Co-op City                    0                   0                    0   
Eastchester                   0                   0                    0   
Eastchester                   0                   0                    0   
Eastchester                   0                   0                    0   

              Arepa Restaurant  Argentinian Restaurant  Asian Restaurant  \
Neighborhood                                                               
Co-op City                   0                       0                 0   
Co-op City                   0                       0                 0   
Eastchester                  0                       0                 0   
Eastchester                  0                       0                 0   
Eastchester                  0                       0                 0   

              Australian Restaurant  Austrian Restaurant  \
Neighborhood                                               
Co-op City                        0                    0   
Co-op City                        0                    0   
Eastchester                       0                    0   
Eastchester                       0                    0   
Eastchester                       0                    0   

              Brazilian Restaurant  Cajun / Creole Restaurant  \
Neighborhood                                                    
Co-op City                       0                          0   
Co-op City                       0                          0   
Eastchester                      0                          0   
Eastchester                      0                          0   
Eastchester                      0                          0   

              Cambodian Restaurant  Cantonese Restaurant  \
Neighborhood                                               
Co-op City                       0                     0   
Co-op City                       0                     0   
Eastchester                      0                     0   
Eastchester                      0                     0   
Eastchester                      0                     0   

              Caribbean Restaurant  Caucasian Restaurant  Chinese Restaurant  \
Neighborhood                                                                   
Co-op City                       0                     0                   0   
Co-op City                       0                     0                   0   
Eastchester                      1                     0                   0   
Eastchester                      0                     0                   0   
Eastchester                      1                     0                   0   

              Colombian Restaurant  Comfort Food Restaurant  Cuban Restaurant  \
Neighborhood                                                                    
Co-op City                       0                        0                 0   
Co-op City                       0                        0                 0   
Eastchester                      0                        0                 0   
Eastchester                      0                        0                 0   
Eastchester                      0                        0                 0   

              Czech Restaurant  Dim Sum Restaurant  Dumpling Restaurant  \
Neighborhood                                                              
Co-op City                   0                   0                    0   
Co-op City                   0                   0                    0   
Eastchester                  0                   0                    0   
Eastchester                  0                   0                    0   
Eastchester                  0                   0                    0

In [150]:
# Grouping by neighborhood
newyork_count_total = newyork_rest.groupby('Neighborhood').count().reset_index()
newyork_count_total.rename(columns = {'Afghan Restaurant': 'Count Total'}, inplace = True)
newyork_count_total = newyork_count_total.iloc[:, 0:2]
newyork_count_total.head()

Neighborhood  Count Total
0     Allerton            4
1     Annadale            4
2    Arlington            1
3     Arrochar            5
4      Arverne            2

In [152]:
# Checking for just Indian Restaurants
newyork_rest_indian = newyork_onehot.filter(like='Indian',axis=1) # filtering just Indian restaurants
newyork_rest_indian = newyork_rest_indian[(newyork_rest_indian.T != 0).any()] # deleting all entries not containing any Indian Restaurants

newyork_count_ind = newyork_rest_indian.groupby('Neighborhood').count().reset_index()
newyork_count_ind.rename(columns = {'Indian Restaurant': 'Count Indian'}, inplace = True)
newyork_count_ind = newyork_count_ind.iloc[:, 0:2]

newyork_count_ind.head()

Neighborhood  Count Indian
0      Astoria             4
1    Bay Ridge             1
2      Bayside             3
3  Boerum Hill             1
4    Briarwood             1

In [143]:
# Downloading the neighborhood boudaries json
!wget -q -O 'newyork_neighborhood_data.json' https://raw.githubusercontent.com/veltman/snd3/master/data/nyc-neighborhoods.geo.json
print('Data downloaded!')

Data downloaded!


In [144]:
with open('newyork_neighborhood_data.json') as json_data:
    newyork_neighborhood_data = json.load(json_data)

In [230]:
# create a numpy array of length 6 and has linear spacing from the minium total number of restaurants to the maximum
threshold_scale = np.linspace(newyork_count_total['Count Total'].min(),
                              newyork_count_total['Count Total'].max(),
                              6, dtype=int)
threshold_scale = threshold_scale.tolist() # change the numpy array to a list
threshold_scale[-1] = threshold_scale[-1] + 1 # make sure that the last value of the list is greater than the maximum immigration

# let Folium determine the scale.
newyork_map = folium.Map(location=[latitude, longitude], zoom_start=11)
newyork_map.choropleth(
    geo_data=newyork_neighborhood_data,
    data=newyork_count_total,
    columns=['Neighborhood', 'Count Total'],
    key_on='feature.properties.name',
    threshold_scale=threshold_scale,
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Total Number of Restaurants',
    reset=True
)
newyork_map

for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(newyork_map)
    
newyork_map

In [155]:
# create a numpy array of length 6 and has linear spacing from the minium total number of Indian restaurants to the maximum
threshold_scale = np.linspace(newyork_count_ind['Count Indian'].min(),
                              newyork_count_ind['Count Indian'].max(),
                              6, dtype=int)
threshold_scale = threshold_scale.tolist() # change the numpy array to a list
threshold_scale[-1] = threshold_scale[-1] + 1 # make sure that the last value of the list is greater than the maximum immigration

# let Folium determine the scale.
newyork_map_indian = folium.Map(location=[latitude, longitude], zoom_start=11)
newyork_map_indian.choropleth(
    geo_data=newyork_neighborhood_data,
    data=newyork_count_ind,
    columns=['Neighborhood', 'Count Indian'],
    key_on='feature.properties.name',
    threshold_scale=threshold_scale,
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Total Number of Restaurants',
    reset=True
)

for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(newyork_map_indian)
    
newyork_map_indian

We see a lot of neighborhoods that have a low number of Indian restaurants also have a low number of total restaurants.
These areas might not be the ones which have a high demand for restaurants and thus are not important to us.
In order to get highlight the areas with low number of Indian but high number of total restaurants, we make a new column called 'Ratio'
Ratio is defined as the number of Indian restaurants in the area / number of total restaurants in the area.

In [232]:
restaurant_ratio = pd.merge(newyork_count_ind, newyork_count_total, how='right', on = 'Neighborhood') # Creating a new dataframe for the ratio column
restaurant_ratio = restaurant_ratio.replace(np.nan, 0) 
restaurant_ratio['Ratio'] = restaurant_ratio['Count Indian'] / restaurant_ratio['Count Total']
restaurant_ratio.head()

Neighborhood  Count Indian  Count Total     Ratio
0      Astoria           4.0           38  0.105263
1    Bay Ridge           1.0           29  0.034483
2      Bayside           3.0           27  0.111111
3  Boerum Hill           1.0           15  0.066667
4    Briarwood           1.0            1  1.000000

In [177]:
threshold_scale = np.linspace(restaurant_ratio['Ratio'].min(),
                              restaurant_ratio['Ratio'].max(),
                              4, dtype=float)
threshold_scale = threshold_scale.tolist() # change the numpy array to a list

# let Folium determine the scale.
newyork_map_ratio = folium.Map(location=[latitude, longitude], zoom_start=11)
newyork_map_ratio.choropleth(
    geo_data=newyork_neighborhood_data,
    data=restaurant_ratio,
    columns=['Neighborhood', 'Ratio'],
    key_on='feature.properties.name',
    threshold_scale=threshold_scale,
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Total Number of Restaurants',
    reset=True
)

for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(newyork_map_ratio)
    
newyork_map_ratio

Looks like a lot of areas lie in the lower ranges of the ratio column. One way to go ahead is to look at only the areas with the lowest number of Indian Restaurants, i.e. 0
In order to do this, let's create a new dataframe with just the neighborhoods with 0 Indian restaurants.

In [215]:
df = restaurant_ratio[restaurant_ratio.Ratio == 0]
df.drop(['Bin'], axis = 1, inplace = True)
df.head()

Neighborhood  Count Indian  Count Total  Ratio
44     Allerton           0.0            4    0.0
45     Annadale           0.0            4    0.0
46    Arlington           0.0            1    0.0
47     Arrochar           0.0            5    0.0
48      Arverne           0.0            2    0.0

In order to shortlist further, we can build on the same idea that we used earlier, i.e., concentrate on the areas which have a high number of total restaurants but a low number of Indian restaurants (in this case, zero). This would ensure that there is enough demand in the area for food in general but no competitors for Indian food.


To do this, we create a new dataframe called shortlist, looking at the top 5 neighborhoods with the most number of restaurants but no Indian restaurant.

In [219]:
shortlist = df.sort_values(by=['Count Total'], ascending=False).head()
shortlist

Neighborhood  Count Indian  Count Total  Ratio
144  Jackson Heights           0.0           39    0.0
77         Chinatown           0.0           37    0.0
101     East Village           0.0           35    0.0
156     Little Italy           0.0           32    0.0
230       South Side           0.0           30    0.0

These seem to be in similar range in terms of the number of total restaurants (at least the top 3 are very close to each other.)

Let's now look at all the venues in these 5 neighborhoods to find the optimal location.

In [221]:
shortlist_venues = pd.merge(shortlist, newyork_onehot, how='left', on = 'Neighborhood') # Getting all the venues for these 5 neighborhoods
shortlist_venues.head()

Neighborhood  Count Indian  Count Total  Ratio  Accessories Store  \
0  Jackson Heights           0.0           39    0.0                  0   
1  Jackson Heights           0.0           39    0.0                  0   
2  Jackson Heights           0.0           39    0.0                  0   
3  Jackson Heights           0.0           39    0.0                  0   
4  Jackson Heights           0.0           39    0.0                  0   

   Adult Boutique  Afghan Restaurant  African Restaurant  Airport Terminal  \
0               0                  0                   0                 0   
1               0                  0                   0                 0   
2               0                  0                   0                 0   
3               0                  0                   0                 0   
4               0                  0                   0                 0   

   American Restaurant  Antique Shop  Arcade  Arepa Restaurant  \
0                    0             0       0                 0   
1                    0             0       0                 0   
2                    0             0       0                 0   
3                    0             0       0                 0   
4                    0             0       0                 0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Arts & Entertainment  Asian Restaurant  Athletics & Sports  Auditorium  \
0                     0                 0                   0           0   
1                     0                 0                   0           0   
2                     0                 0                   0           0   
3                     0                 0                   0           0   
4                     0                 0                   0           0   

   Australian Restaurant  Austrian Restaurant  Automotive Shop  BBQ Joint  \
0                      0                    0                0          0   
1                      0                    0                0          0   
2                      0                    0                0          0   
3                      0                    0                0          0   
4                      0                    0                0          0   

   Baby Store  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0           0           0       0     0    0               0   
1           0           0       0     0    0               0   
2           0           0       0     0    0               0   
3           0           0       0     0    0               0   
4           0           0       0     0    0               0   

   Baseball Stadium  Basketball Court  Basketball Stadium  Bath House  Beach  \
0                 0                 0                   0           0      0   
1                 0                 0                   0           0      0   
2                 0                 0                   0           0      0   
3                 0                 0                   0           0      0   
4                 0                 0                   0           0      0   

   Beach Bar  Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  \
0          0                0         0            0           0   
1          0                0         0            0           0   
2          0                0         0            0           0   
3          0                0         0            0           0   
4          0                0         0            0           0   

   Big Box Store  Bike Rental / Bike 

In [225]:
# Grouping by neighborhoods and finding the frequency of the occurence of venues in these 5 neighborhoods
shortlist_grouped = shortlist_venues.groupby('Neighborhood').mean().reset_index() 
shortlist_grouped

Neighborhood  Count Indian  Count Total  Ratio  Accessories Store  \
0        Chinatown           0.0           37    0.0                0.0   
1     East Village           0.0           35    0.0                0.0   
2  Jackson Heights           0.0           39    0.0                0.0   
3     Little Italy           0.0           32    0.0                0.0   
4       South Side           0.0           30    0.0                0.0   

   Adult Boutique  Afghan Restaurant  African Restaurant  Airport Terminal  \
0             0.0                0.0                 0.0               0.0   
1             0.0                0.0                 0.0               0.0   
2             0.0                0.0                 0.0               0.0   
3             0.0                0.0                 0.0               0.0   
4             0.0                0.0                 0.0               0.0   

   American Restaurant  Antique Shop  Arcade  Arepa Restaurant  \
0                 0.03           0.0     0.0              0.00   
1                 0.01           0.0     0.0              0.01   
2                 0.00           0.0     0.0              0.00   
3                 0.00           0.0     0.0              0.00   
4                 0.06           0.0     0.0              0.01   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                  0.0000         0.00         0.0                 0.00   
1                  0.0100         0.01         0.0                 0.01   
2                  0.0125         0.00         0.0                 0.00   
3                  0.0000         0.00         0.0                 0.01   
4                  0.0000         0.01         0.0                 0.00   

   Arts & Entertainment  Asian Restaurant  Athletics & Sports  Auditorium  \
0                   0.0            0.0200                 0.0         0.0   
1                   0.0            0.0000                 0.0         0.0   
2                   0.0            0.0125                 0.0         0.0   
3                   0.0            0.0000                 0.0         0.0   
4                   0.0            0.0000                 0.0         0.0   

   Australian Restaurant  Austrian Restaurant  Automotive Shop  BBQ Joint  \
0                   0.00                 0.01              0.0       0.00   
1                   0.00                 0.00              0.0       0.00   
2                   0.00                 0.00              0.0       0.00   
3                   0.01                 0.00              0.0       0.00   
4                   0.00                 0.00              0.0       0.01   

   Baby Store  Bagel Shop  Bakery    Bank     Bar  Baseball Field  \
0         0.0        0.00    0.06  0.0000  0.0300             0.0   
1         0.0        0.02    0.01  0.0000  0.0700             0.0   
2         0.0        0.00    0.05  0.0125  0.0125             0.0   
3         0.0        0.01    0.06  0.0000  0.0000             0.0   
4         0.0        0.01    0.02  0.0000  0.0800             0.0   

   Baseball Stadium  Basketball Court  Basketball Stadium  Bath House  Beach  \
0               0.0               0.0                 0.0         0.0    0.0   
1               0.0               0.0                 0.0         0.0    0.0   
2               0.0               0.0                 0.0         0.0    0.0   
3               0.0               0.0                 0.0         0.0    0.0   
4               0.0               0.0                 0.0         0.0    0.0   

   Beach Bar  Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  \
0        0.0              0.0      0.00         0.00        0.00   
1        0.0              0.0      0.01         0.00        0.01   
2        0.0              0.0      0.00         0.00        0.00   
3        0.0              0.0      0.00         0.00        0.00   
4        0.0              0.0      0.00         0.01        0.00   

   Big 

In [233]:
# Looking at the top 5 venues in these locations
num_top_venues = 5

for hood in shortlist_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = shortlist_grouped[shortlist_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Chinatown----
                venue   freq
0         Count Total  37.00
1  Chinese Restaurant   0.08
2              Bakery   0.06
3        Dessert Shop   0.04
4   Hotpot Restaurant   0.03


----East Village----
                venue   freq
0         Count Total  35.00
1                 Bar   0.07
2  Mexican Restaurant   0.05
3         Pizza Place   0.05
4        Cocktail Bar   0.05


----Jackson Heights----
                       venue   freq
0                Count Total  39.00
1  Latin American Restaurant   0.11
2        Peruvian Restaurant   0.08
3  South American Restaurant   0.06
4                     Bakery   0.05


----Little Italy----
                venue   freq
0         Count Total  32.00
1              Bakery   0.06
2  Chinese Restaurant   0.06
3                 Spa   0.04
4  Italian Restaurant   0.04


----South Side----
                 venue   freq
0          Count Total  30.00
1                  Bar   0.08
2          Coffee Shop   0.07
3  American Restaurant   0.06
4

### Final analysis on these 5 shortlisted venues:
One reason for no occurence of an Indian restaurant in these locations could be because these might be popular for a certain cuisine and thus the demand for food is also majorly for that one specialised cuisine.


It would be best for us to find the neighborhood which is the most neutral in terms of the frequency of occurence of different types of venues. In order to determine the most neutral location, let's look at the venue with the highest frequency of occurence as a percentage.

1. Chinatown: Chinese restaurants comprise 8% of total venues in the neighborhood.
2. East Village: Bars comprise 7% of total venues in the neighborhood.
3. Jackson Heights: Latin American restaurants comprise 11% of total venues in the neighborhood.
4. Little Italy: Bakeries comprise 6% of total venues in the neighborhood.
5. South side: Bars comprise 8% of total venues in the neighborhood.

Looks like **Little Italy** and **East Village** are the optimal neighborhoods to open an Indian Restaurant